![](https://github.com/bigdata-icict/ETL-Dataiku-DSS/raw/master/tutoriais/pcdas_1.5.png)

# Notebook para criação de tabela de indicadores da PNS - módulo O 2013 Acidentes

## Bibliotecas Utilizadas

In [ ]:
#Lendo pacotes necessários
library(survey)
library(dplyr)
library(tictoc)
library(foreign)
library(forcats)
library(tidyverse)

## Carregando microdados da PNS

In [ ]:
#Carregando banco de dados
load("<coloque aqui o caminho para o arquivo dos microdados formato RDATA>")

## Definição do peso e filtragem de respondentes do questionário

In [3]:
#Selecionando registros válidos para o módulo P e calculando peso amostral - summary de verificação
pns2013.1<-pns2013 %>% filter(M001==1)
pns2013.1<-pns2013.1 %>% mutate(peso_morador_selec=((V00291*(60202/145572211))))
pns2013.1<-pns2013.1 %>% filter(!is.na(peso_morador_selec))
summary(pns2013.1$peso_morador_selec)

     Min.   1st Qu.    Median      Mean   3rd Qu.      Max. 
 0.004156  0.243959  0.521557  1.000000  1.147413 31.179597 

## Criação de variáveis dos indicadores

In [4]:
#Usa sempre cinto quando anda no banco de trás de automóvel. - O002P
pns2013.1 <- pns2013.1 %>% mutate(O002P=ifelse(O005==1, NA, ifelse(O005==2, 1, 2)))
pns2013.1$O002P<-factor(pns2013.1$O002P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2013.1$O002P)

#Usa sempre capacete quando dirige motocicleta. - O003P

pns2013.1 <- pns2013.1 %>% mutate(O003P= ifelse(O007==1, 1, 2))
pns2013.1$O003P<-factor(pns2013.1$O003P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2013.1$O003P)

#Usa sempre capacete quando está como passageiro de motocicleta. - O004P
pns2013.1 <- pns2013.1  %>% mutate(O004P= ifelse(O008==1,NA,ifelse(O008==2,1,2)))
pns2013.1$O004P<-factor(pns2013.1$O004P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2013.1$O004P)

#Usa sempre capacete quando está como passageiro de motocicleta. - O006P
pns2013.1 <- pns2013.1  %>% mutate(O006P = ifelse(O009==1,1,
                                          ifelse(O009==2,2,2)))   
pns2013.1$O006P<-factor(pns2013.1$O006P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2013.1$O006P)

Sim   Não  NA's 
25855 27307  7040

Sim   Não  NA's 
11780  2547 45875

Sim   Não  NA's 
24130  5687 30385

Sim   Não 
 1910 58292

## Definições de abrangências

### Situação urbana ou rural

In [5]:
#Situação Urbano ou Rural
pns2013.1 <- pns2013.1 %>% rename(Sit_Urbano_Rural=V0026)
pns2013.1$Sit_Urbano_Rural<-factor(pns2013.1$Sit_Urbano_Rural, levels=c(1,2), labels=c("urbano", "rural"))
summary(pns2013.1$Sit_Urbano_Rural)

urbano  rural 
 49245  10957

### Sexo

In [6]:
#Sexo
pns2013.1 <- pns2013.1 %>% rename(Sexo=C006)
pns2013.1$Sexo<-factor(pns2013.1$Sexo, levels=c(1,2), labels=c("Masculino", "Feminino"))
summary(pns2013.1$Sexo)

Masculino  Feminino 
    25920     34282

### UF

In [7]:
#Estados - UFs
pns2013.1 <- pns2013.1 %>% rename(Unidades_da_Federacao=V0001)
pns2013.1$Unidades_da_Federacao<-factor(pns2013.1$Unidades_da_Federacao, levels=c(11,12,13,14,15,16,17,21,22,23,24,25,26,27,28,29,31,32,33,35,41,42,43,50,51,52,53),
                                       label=c("Rondônia","Acre","Amazonas","Roraima","Pará","Amapá","Tocantins","Maranhão","Piauí","Ceará",
                                        "Rio Grande do Norte","Paraíba","Pernambuco","Alagoas","Sergipe","Bahia",
                                        "Minas Gerais","Espírito Santo","Rio de Janeiro","São Paulo",
                                        "Paraná","Santa Catarina","Rio Grande do Sul", 
                                        "Mato Grosso do Sul","Mato Grosso","Goiás","Distrito Federal"))
summary(pns2013.1$Unidades_da_Federacao)

Rondônia                Acre            Amazonas             Roraima 
               1694                1814                2586                1591 
               Pará               Amapá           Tocantins            Maranhão 
               2004                1332                1515                1774 
              Piauí               Ceará Rio Grande do Norte             Paraíba 
               1804                2560                1691                1943 
         Pernambuco             Alagoas             Sergipe               Bahia 
               2591                1748                1553                2641 
       Minas Gerais      Espírito Santo      Rio de Janeiro           São Paulo 
               3779                1724                3486                5305 
             Paraná      Santa Catarina   Rio Grande do Sul  Mato Grosso do Sul 
               3012                1623                2913                1809 
        Mato Grosso               Goiás    Distrito Federal 
               1476                2423                1811

### Grandes Regiões

In [8]:
#Grandes Regiões
pns2013.1 <- pns2013.1 %>% 
  mutate(GrandesRegioes = fct_collapse(Unidades_da_Federacao, 
                                          `Norte` = c("Rondônia","Acre","Amazonas","Roraima","Pará", "Amapá","Tocantins"),
                                          `Nordeste` = c("Maranhão", "Piauí", "Ceará", "Rio Grande do Norte", "Paraíba","Pernambuco", "Alagoas","Sergipe","Bahia"),
                                          `Sudeste` = c("Minas Gerais", "Espírito Santo","Rio de Janeiro", "São Paulo"), 
                                          `Sul` = c("Paraná", "Santa Catarina", "Rio Grande do Sul"),
                                          `Centro-Oeste`= c("Mato Grosso do Sul","Mato Grosso", "Goiás", "Distrito Federal")))
summary(pns2013.1$GrandesRegioes)

Norte     Nordeste      Sudeste          Sul Centro-Oeste 
       12536        18305        14294         7548         7519

### Faixa Etária

In [9]:
#Faixas Etárias
pns2013.1 <-  pns2013.1 %>% mutate(faixa_idade=cut(C008,
  breaks = c(18,30, 45, 60,Inf),
  labels = c("18 a 29 anos","30 a 44 anos","45 a 59 anos","60 anos ou mais"), 
  ordered_result = TRUE, right = FALSE))
summary(pns2013.1$faixa_idade) 

18 a 29 anos    30 a 44 anos    45 a 59 anos 60 anos ou mais 
          14321           20242           14462           11177

### Raça

In [10]:
#Raça
pns2013.1 <- pns2013.1 %>% mutate(Raca= ifelse(C009==1, 1, 
                                        ifelse(C009==2, 2, 
                                        ifelse(C009==4, 3, 9))))

pns2013.1$Raca<-factor(pns2013.1$Raca, levels=c(1,2,3),labels=c("Branca", "Preta", "Parda"))

summary(pns2013.1$Raca)

Branca  Preta  Parda   NA's 
 24106   5631  29512    953

### Renda per capita

In [11]:
#Rendimento domiciliar per capita
pns2013.1 <-  pns2013.1  %>% mutate(rend_per_capita=cut(VDF003,
  breaks = c(-Inf,339, 678, 1356, 2034,Inf),
  labels=c("Até 1/2 SM","1/2 até 1 SM","1 até 2 SM","2 até 3 SM","Mais de 3 SM"), 
  ordered_result = TRUE, right = TRUE, na.exclude= TRUE))

summary(pns2013.1$rend_per_capita)

Até 1/2 SM 1/2 até 1 SM   1 até 2 SM   2 até 3 SM Mais de 3 SM         NA's 
       14256        17504        15493         5335         7603           11

### Escolaridade

In [12]:
# Escolaridade
pns2013.1 <- pns2013.1 %>% mutate(gescol = ifelse(VDD004A %in% 1:2, 1, 
                        ifelse(VDD004A%in% 3:4, 2, 
                        ifelse(VDD004A%in% 5:6, 3,4
                        ))))

pns2013.1$gescol<-factor(pns2013.1$gescol, levels=c(1,2,3,4), 
                                   labels=c("Fundamental incompleto ou equivalente","Médio incompleto ou equivalente",
                                           "Superior incompleto ou equivalente","Superior completo"))
summary(pns2013.1$gescol)

Fundamental incompleto ou equivalente       Médio incompleto ou equivalente 
                                24083                                  9215 
   Superior incompleto ou equivalente                     Superior completo 
                                19149                                  7755

### Capital

In [13]:
#Capital
pns2013.1<- pns2013.1 %>% mutate(Capital= fct_collapse(Unidades_da_Federacao,
                                        `Porto Velho`= "Rondônia", 
                                        `Boa Vista`= "Roraima",              
                                        `Rio Branco`= "Acre", 
                                        `Manaus` = "Amazonas",
                                        `Belém` = "Pará" ,
                                        `Macapá`= "Amapá",
                                        `Palmas` = "Tocantins",
                                        `São Luís` = "Maranhão",
                                        `Teresina`= "Piauí" ,
                                        `Fortaleza`= "Ceará",
                                        `Natal`= "Rio Grande do Norte",
                                        `João Pessoa`= "Paraíba",
                                        `Recife`= "Pernambuco",
                                        `Maceió`= "Alagoas",
                                        `Aracaju`= "Sergipe",
                                        `Salvador`= "Bahia",
                                        `Belo Horizonte`= "Minas Gerais",
                                        `Vitória`= "Espírito Santo",
                                        `Rio de Janeiro`= "Rio de Janeiro",
                                        `São Paulo`= "São Paulo",
                                        `Curitiba`= "Paraná",
                                        `Florianópolis`= "Santa Catarina",
                                        `Porto Alegre`= "Rio Grande do Sul",
                                        `Campo Grande`=  "Mato Grosso do Sul",
                                        `Cuiabá`= "Mato Grosso",
                                        `Goiânia` = "Goiás",
                                        `Brasília`= "Distrito Federal"))
summary(pns2013.1$Capital)

Porto Velho     Rio Branco         Manaus      Boa Vista          Belém 
          1694           1814           2586           1591           2004 
        Macapá         Palmas       São Luís       Teresina      Fortaleza 
          1332           1515           1774           1804           2560 
         Natal    João Pessoa         Recife         Maceió        Aracaju 
          1691           1943           2591           1748           1553 
      Salvador Belo Horizonte        Vitória Rio de Janeiro      São Paulo 
          2641           3779           1724           3486           5305 
      Curitiba  Florianópolis   Porto Alegre   Campo Grande         Cuiabá 
          3012           1623           2913           1809           1476 
       Goiânia       Brasília 
          2423           1811

## Criando indicadores

### Filtrando base de indicadores

In [14]:
#Selecionando variáveis para cálculo de indicadores no survey
pns2013Osurvey<- pns2013.1 %>% select("V0024","UPA_PNS","peso_morador_selec", "O002P","O003P","O004P", "O006P",
                                     "C008","C009","V0031","Sit_Urbano_Rural","Sexo","Unidades_da_Federacao", "GrandesRegioes",
                                     "faixa_idade", "Raca","rend_per_capita",,"gescol","Capital")
summary(pns2013Osurvey)

     V0024            UPA_PNS        peso_morador_selec   O002P      
 Min.   :1110011   Min.   :1100001   Min.   : 0.004156   Sim :25855  
 1st Qu.:2210013   1st Qu.:2200075   1st Qu.: 0.243959   Não :27307  
 Median :2951023   Median :2900192   Median : 0.521557   NA's: 7040  
 Mean   :3035353   Mean   :3007819   Mean   : 1.000000               
 3rd Qu.:4110111   3rd Qu.:4100002   3rd Qu.: 1.147413               
 Max.   :5310220   Max.   :5300180   Max.   :31.179597               
                                                                     
  O003P        O004P       O006P            C008             C009     
 Sim :11780   Sim :24130   Sim: 1910   Min.   : 18.00   Min.   :1.00  
 Não : 2547   Não : 5687   Não:58292   1st Qu.: 30.00   1st Qu.:1.00  
 NA's:45875   NA's:30385               Median : 41.00   Median :3.00  
                                       Mean   : 43.31   Mean   :2.61  
                                       3rd Qu.: 55.00   3rd Qu.:4.00  
              

### Cria plano amostral complexo

In [15]:
#Salvando csv para cálculo de indicadores no survey
path <- "../dados"
write.csv(pns2013Osurvey, file.path(path, "pns2013Osurvey.csv"))

In [16]:
desPNSO=svydesign(id=~UPA_PNS, strat=~V0024, weight=~peso_morador_selec, nest=TRUE, data=pns2013Osurvey)

In [17]:
#survey design -O002P
desPNSO002P_18=subset(desPNSO, C008>=18 & !is.na(O002P))
desPNSO002P_R18=subset(desPNSO, C008>=18 & !is.na(O002P) & !is.na(Raca))
desPNSO002P_C18=subset(desPNSO, C008>=18 & V0031==1 & !is.na(O002P))
desPNSO002P_RC18=subset(desPNSO, C008>=18  & !is.na(O002P) & !is.na(rend_per_capita))

In [18]:
#survey design -O003P
desPNSO003P_18=subset(desPNSO, C008>=18 & !is.na(O003P))
desPNSO003P_R18=subset(desPNSO, C008>=18 & !is.na(O003P) & !is.na(Raca))
desPNSO003P_C18=subset(desPNSO, C008>=18 & V0031==1 & !is.na(O003P))
desPNSO003P_RC18=subset(desPNSO, C008>=18  & !is.na(O003P) & !is.na(rend_per_capita))

In [19]:
#survey design -O004P
desPNSO004P_18=subset(desPNSO, C008>=18 & !is.na(O004P))
desPNSO004P_R18=subset(desPNSO, C008>=18 & !is.na(O004P) & !is.na(Raca))
desPNSO004P_C18=subset(desPNSO, C008>=18 & V0031==1 & !is.na(O004P))
desPNSO004P_RC18=subset(desPNSO, C008>=18  & !is.na(O004P) & !is.na(rend_per_capita))

In [20]:
#survey design -O006P
desPNSO006P_18=subset(desPNSO, C008>=18)
desPNSO006P_R18=subset(desPNSO, C008>=18 & !is.na(Raca))
desPNSO006P_C18=subset(desPNSO, C008>=18 & V0031==1)
desPNSO006P_RC18=subset(desPNSO, C008>=18 & !is.na(rend_per_capita))

### Criação da tabela de indicadores
Essa tabela é responsável por unir os indicadores no formato do painel de indicadores

In [21]:
matrizIndicadores = data.frame()

#### Definição de variáveis para iteração dos indicadores

In [22]:
ListaIndicadores = c(~O002P,~O003P,~O004P,~O006P)
ListaIndicadoresTexto = c("O002P","O003P","O004P","O006P")
ListaDominios = c(~Sexo,~Raca,~rend_per_capita,~faixa_idade,~Sit_Urbano_Rural,~Unidades_da_Federacao,~GrandesRegioes,~gescol,~Capital)
ListaDominiosTexto = c("sexo","raça","rend_per_capita","fx_idade_acid","urb_rur","uf","região","gescol","capital")
ListaTotais = c('Brasil','Capital')
Ano <- "2013"

#### Preenchendo a tabela de indicadores
Essas iterações rodam por indicador, abrangência e por design

In [23]:
#Cálculo dos indicadores usando o pacote survey 
i <- 0
#Para cada indicador
for( indicador in ListaIndicadores){
    i <- i + 1
    j <- 1
    #Para cada dominio
    for (dominio in ListaDominios){
               #design especifico para capital que é subconjunto do dataframe total
               if (ListaDominiosTexto[j]=="capital"){
                   #designs especificos por variavel que são subconjuntos do dataset total
                   if(ListaIndicadoresTexto[i] == "O002P"){
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO002P_C18 , svymean,vartype= c("ci", "cv"))
                   }
                   else if(ListaIndicadoresTexto[i] == "O003P"){
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO003P_C18 , svymean,vartype= c("ci", "cv"))
                   }else if(ListaIndicadoresTexto[i] == "O004P"){# cv maior do que o aceitável
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO004P_C18 , svymean,vartype= c("ci", "cv"))
                   }else{
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO006P_C18 , svymean,vartype= c("ci", "cv"))
                   }
               #Uso design do subconjunto para raça/cor que inclui preta,branca e parda as outras 
               #não possuiam dados suficientes para os dominios dos indicadores
               }else if (ListaDominiosTexto[j]=="raça"){
                   if(ListaIndicadoresTexto[i] == "O002P"){
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO002P_R18 , svymean,vartype= c("ci", "cv"))
                   }
                   else if(ListaIndicadoresTexto[i] == "O003P"){
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO003P_R18 , svymean,vartype= c("ci", "cv"))
                   }else if(ListaIndicadoresTexto[i] == "O004P"){
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO004P_R18 , svymean,vartype= c("ci", "cv"))
                   }
                   else{
                       dataframe_indicador<-svyby( indicador , dominio , desPNSO006P_R18 , svymean,vartype= c("ci", "cv"))
                   }
               #design geral para o subconjunto maior que 18 anos
               }else if (ListaDominiosTexto[j]=="rend_per_capita"){
                   if(ListaIndicadoresTexto[i] == "O002P"){
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO002P_RC18 , svymean,vartype= c("ci", "cv"))
                   }
                   else if(ListaIndicadoresTexto[i] == "O003P"){
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO003P_RC18 , svymean,vartype= c("ci", "cv"))
                   }else if(ListaIndicadoresTexto[i] == "O004P"){
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO004P_RC18 , svymean,vartype= c("ci", "cv"))
                   }
                       else{dataframe_indicador<-svyby( indicador , dominio , desPNSO006P_RC18 , svymean,vartype= c("ci", "cv"))}
               #design geral para o subconjunto maior que 18 anos
               }else {
                   if(ListaIndicadoresTexto[i] == "O002P"){
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO002P_18 , svymean,vartype= c("ci", "cv"))
                   }
                   else if(ListaIndicadoresTexto[i] == "O003P"){
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO003P_18 , svymean,vartype= c("ci", "cv"))
                   }else if(ListaIndicadoresTexto[i] == "O004P"){
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO004P_18 , svymean,vartype= c("ci", "cv"))
                   }else{
                     dataframe_indicador<-svyby( indicador , dominio , desPNSO006P_18 , svymean,vartype= c("ci", "cv"))
                   }
               }
               #União do dataframe de indicadores no formato do painel disponibilizado para PNS
               
               dataframe_indicador<-data.frame(dataframe_indicador)
               
               colnames(dataframe_indicador) <- c("abr_nome","Sim","Nao","LowerS","LowerN","UpperS","UpperN","cvS","cvN")
               dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
               dataframe_indicador$abr_tipo <- ListaDominiosTexto[j]
               dataframe_indicador$Ano <- Ano
               dataframe_indicador <- dataframe_indicador %>% select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS","cvS")
               matrizIndicadores <-rbind(matrizIndicadores,dataframe_indicador)
               j <- j + 1
    }
}

#### Criando a tabela pela abrangência total

In [24]:
matriz_totais <- data.frame()

#### Preenchendo a tabela com as abrangencia Brasil e total das capitais

In [ ]:
i=0
#para cada indicador
for(indicador in ListaIndicadores){
    i <- i+1
    #para os totais Brasil e total das capitais
    for(total in ListaTotais){
        #Uso do design que é subconjunto do dataset para cada Capital
        if (total == "Capital"){
                   #Indicadores que são subconjunto do dataset tot
                   if(ListaIndicadoresTexto[i] == "O002P"){
                           dataframe_indicador <- svymean(indicador,desPNSO002P_C18)
                   }else if(ListaIndicadoresTexto[i] == "O003P"){
                           dataframe_indicador <- svymean(indicador,desPNSO003P_C18)
                   }else if(ListaIndicadoresTexto[i] == "O004P"){
                           dataframe_indicador <- svymean(indicador,desPNSO004P_C18)
                   }else{
                       dataframe_indicador <- svymean(indicador,desPNSO006P_C18)
                   }
                   
        } else {
                   if(ListaIndicadoresTexto[i] == "O002P"){
                           dataframe_indicador <- svymean(indicador,desPNSO002P_18)
                   }else if(ListaIndicadoresTexto[i] == "O003P"){
                           dataframe_indicador <- svymean(indicador,desPNSO003P_18)
                   }else if(ListaIndicadoresTexto[i] == "O004P"){
                           dataframe_indicador <- svymean(indicador,desPNSO004P_18)
                   }else{
                       dataframe_indicador <- svymean(indicador,desPNSO006P_18)
                   }
        }
      
        intervalo_confianca <- confint(dataframe_indicador)
        coeficiente_variacao <- cv(dataframe_indicador)
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(intervalo_confianca))
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(coeficiente_variacao))
        
        dataframe_indicador <- dataframe_indicador %>% 
                               select('mean','X2.5..','X97.5..',coeficiente_variacao) 
        dataframe_indicador_S <- dataframe_indicador %>% 
                                 slice(1)
                
        colnames(dataframe_indicador_S) <- c('Sim','LowerS','UpperS', 'cvS')
        dataframe_indicador_S$Indicador <- ListaIndicadoresTexto[i]
        print(ListaIndicadoresTexto[i])
        dataframe_indicador_S$abr_tipo <- "total"
        dataframe_indicador_S$abr_nome <- total
        dataframe_indicador_S$Ano <- Ano 
        print(colnames(dataframe_indicador_S))
        dataframe_indicador_S <- dataframe_indicador_S %>% 
                             select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS",'cvS')
        
        matriz_totais <-rbind(matriz_totais,dataframe_indicador_S)
        
    }
}

#### Unindo tabela de indicadores e de totais

In [44]:
matrizIndicadores<-rbind(matrizIndicadores,matriz_totais)

#### Exportando tabela de indicadores

In [46]:
write.table(matrizIndicadores,file="<coloque aqui o caminho para exportação da matriz de indicadores>",sep = ";",dec = ",",row.names = FALSE)